In [4]:
#importing some useful packages
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import numpy as np
import cv2
import os
import imageio
imageio.plugins.ffmpeg.download()
from moviepy.editor import * # imports everything, quick and dirty
import moviepy.editor as mpy # Clean. Then use mpy.VideoClip, etc.
from moviepy.editor import VideoFileClip # just import what you need
from IPython.display import HTML

# Declaring Gloabal Variables
Catch_left_slope = 0
Catch_right_slope  = 0
Catch_left  = [0, 0, 0]
Catch_right  = [0, 0, 0]
vertices = [0,0,0,0]

def reset_globals():
    """
    Clear your globals before using new outputs
    """
    print("RESETING GLOBAL VALUES")
    global Catch_left_slope 
    global Catch_right_slope 
    global Catch_left   # X1, Y1, X2
    global Catch_right  
    global vertices
    Catch_left_slope  = 0
    Catch_right_slope  = 0
    Catch_left= [0, 0, 0]  # X1, Y1, X2
    Catch_right = [0, 0, 0]
    vertices = [0,0,0,0]
    
def draw_lines(img, lines, color=[255, 0, 0], thickness=20):
   
    global Catch_left_slope 
    global Catch_right_slope
    global Catch_left
    global Catch_right
    
    # DECLARE VARIABLES
    cache_weight = 0.9
    right_ys = []
    right_xs = []
    right_slopes = []

    left_ys = []
    left_xs = []
    left_slopes = []
    
    midpoint = img.shape[1] / 2  # X/2
    bottom_of_image = img.shape[0]  # Y
    
    for line in lines:
        for x1,y1,x2,y2 in line:   
            slope, intercept = np.polyfit((x1,x2), (y1,y2), 1)
            # Seprate points, and slope, lines
            if .35 < np.absolute(slope) <= .85: # Take all position and negative slopes
                if slope > 0 and x1 > midpoint and x2 > midpoint:
                    right_ys.append(y1)
                    right_ys.append(y2)
                    right_xs.append(x1)
                    right_xs.append(x2)
                    right_slopes.append(slope)
                elif slope < 0 and x1 < midpoint and x2 < midpoint:
                    left_ys.append(y1)
                    left_ys.append(y2)
                    left_xs.append(x1)
                    left_xs.append(x2)
                    left_slopes.append(slope)
                    
    # Identify and Draw Right Lane Line
    if right_ys:
        right_index = right_ys.index(min(right_ys))  #index of y min wil be index of x min
        right_x1 = right_xs[right_index]
        right_y1 = right_ys[right_index]
        right_slope = np.median(right_slopes)
        if Catch_right_slope != 0:
            right_slope = right_slope + (Catch_right_slope - right_slope) * cache_weight

        right_x2 = int(right_x1 + (bottom_of_image - right_y1) / right_slope)
        
        if Catch_right_slope != 0:
            right_x1 = int(right_x1 + (Catch_right[0] - right_x1) * cache_weight)
            right_y1 = int(right_y1 + (Catch_right[1] - right_y1) * cache_weight)
            right_x2 = int(right_x2 + (Catch_right[2] - right_x2) * cache_weight)

        Catch_right_slope = right_slope
        Catch_right = [right_x1, right_y1, right_x2]

        cv2.line(img, (right_x1, right_y1), (right_x2, bottom_of_image), color, thickness)
        
    # Identify and Draw Left Lane Line
    if left_ys:
        left_index = left_ys.index(min(left_ys))
        left_x1 = left_xs[left_index]
        left_y1 = left_ys[left_index]
        left_slope = np.median(left_slopes)
        if Catch_left_slope != 0:
            left_slope = left_slope + (Catch_left_slope - left_slope) * cache_weight

        left_x2 = int(left_x1 + (bottom_of_image - left_y1) / left_slope)

        if Catch_left_slope != 0:
            left_x1 = int(left_x1 + (Catch_left[0] - left_x1) * cache_weight)
            left_y1 = int(left_y1 + (Catch_left[1] - left_y1) * cache_weight)
            left_x2 = int(left_x2 + (Catch_left[2] - left_x2) * cache_weight)

        Catch_left_slope = left_slope
        Catch_left = [left_x1, left_y1, left_x2]

        cv2.line(img, (left_x1, left_y1), (left_x2, bottom_of_image), color, thickness)

In [2]:
def process_image(image):

    global vertices
     # Parameters of Process Image
    imshape = image.shape
    kernel_size = 3 #kernel size should be a positive odd integer
    sigma_x = 0
    low_canny_threshold = 65 # reject pixels below the low_threshold
    high_canny_threshold = low_canny_threshold * 3 #detect strong edge (strong gradient) pixels above the high_threshold
    vertices = np.array([[(0,imshape[0]), (9*imshape[1]/20, 11*imshape[0]/18), (11*imshape[1]/20, 11*imshape[0]/18), (imshape[1],imshape[0])]], dtype=np.int32) # For varibale Image Shape
    ignore_mask_color = 255
    rho = 1  # distance resolution in pixels of the Hough grid
    theta = np.pi/180
    hough_threshold = 10 # minimum number of votes (intersections in a given grid cell)
    min_line_len = 100 # Is the minimum length of a line (in pixels) that you will accept in the output (#minimum number of pixels making up a line)
    max_line_gap = 200 #  Is the maximum distance (in pixels) between segments that you will allow to be connected into a single line
    α = 0.7
    β = 1
    λ = 0

    #  Convert Color Image into Gray for processing
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

     # Apply Gaussian Blurr for removing noise from image
    blur = cv2.GaussianBlur(gray, (kernel_size, kernel_size), sigma_x)

    # Apply canny edge algorithem for detecting edges in Image
    # The algorithm will first detect strong edge (strong gradient) pixels above the high_threshold, and reject pixels below the low_threshold. Next, pixels with values between the low_threshold and high_threshold will be included as long as they are connected to strong edges. 
    edges = cv2.Canny(blur, low_canny_threshold, high_canny_threshold)

    # Select Region of Interest of Image and mask rest of it
    mask = np.zeros_like(edges)
    cv2.fillPoly(mask, vertices, ignore_mask_color)
    masked = cv2.bitwise_and(edges, mask)

    # Apply Hough Transform to identify and form lines of interest
    lines = cv2.HoughLinesP(masked, rho, theta, hough_threshold, np.array([]), minLineLength=min_line_len, maxLineGap=max_line_gap)
    hough_image = np.zeros((*masked.shape, 3), dtype=np.uint8)
    draw_lines(hough_image, lines)

    # Weight two Image and get desired output
    result = cv2.addWeighted(image, α, hough_image, β, λ) #initial_img * α + img * β + λ

    return result

In [3]:
imageNames = os.listdir('test_images/')
for name in imageNames:
    reset_globals()
    image = mpimg.imread("test_images/{}".format(name))
    plt.imsave("final_images/final_{}".format(name), process_image(image))

RESETING GLOBAL VALUES
RESETING GLOBAL VALUES
RESETING GLOBAL VALUES
RESETING GLOBAL VALUES
RESETING GLOBAL VALUES
RESETING GLOBAL VALUES


In [9]:
reset_globals()
white_output = 'white.mp4'
clip1 = VideoFileClip("solidWhiteRight.mp4")
white_clip = clip1.fl_image(process_image) #NOTE: this function expects color images!!
%time white_clip.write_videofile(white_output, audio=False)
#white_output.show(10.5) # shows the frame of the clip at t=10.5s
ipython_display( white_clip, width=400)
ipython_display( white_clip, autoplay=1, loop=1)
# #
# HTML("""
# <video width="960" height="540" controls>
#   <source src="{0}">
# </video>
# """.format(white_output))
# #


RESETING GLOBAL VALUES
[MoviePy] >>>> Building video white.mp4
[MoviePy] Writing video white.mp4


100%|███████████████████████████████████████████████████████████████████████████████▋| 221/222 [00:04<00:00, 41.16it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: white.mp4 

Wall time: 5.55 s


100%|███████████████████████████████████████████████████████████████████████████████▋| 221/222 [00:03<00:00, 63.37it/s]


In [11]:
reset_globals()
yellow_output = 'yellow.mp4'
clip2 = VideoFileClip('solidYellowLeft.mp4')
yellow_clip = clip2.fl_image(process_image)
%time yellow_clip.write_videofile(yellow_output, audio=False)
#
# HTML("""
# <video width="960" height="540" controls>
#   <source src="{0}">
# </video>
# """.format(yellow_output))

RESETING GLOBAL VALUES
[MoviePy] >>>> Building video yellow.mp4
[MoviePy] Writing video yellow.mp4


100%|███████████████████████████████████████████████████████████████████████████████▉| 681/682 [00:16<00:00, 40.58it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: yellow.mp4 

Wall time: 17.5 s


In [15]:
reset_globals()
challenge_output = 'extra.mp4'
clip1 = VideoFileClip("challenge.mp4")
challenge_clip = clip1.fl_image(process_image) #NOTE: this function expects color images!!
%time challenge_clip.write_videofile(challenge_output, audio=False)
#Play video inline
#ipython_display( challenge_clip, width=400)
ipython_display( challenge_output, autoplay=1, loop=1)
# HTML("""
# <video width="960" height="540" controls>
#   <source src="{0}">
# </video>
# """.format(challenge_output))

RESETING GLOBAL VALUES
[MoviePy] >>>> Building video extra.mp4
[MoviePy] Writing video extra.mp4


100%|████████████████████████████████████████████████████████████████████████████████| 251/251 [00:12<00:00, 20.76it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: extra.mp4 

Wall time: 13.5 s


Reflection of Assignment 1:

My Lane line detection dosen't work well enough on concrete road surface where color diffrence between solid lane and road surface is less in Challenge.mp3 video. I also saw issue of detecting lane where road reflection is high. I would like to dive deep into this problem and find solution.
